# Data Inspection
This notebook loads the new TWIX scan data and displays a zero-filled k-space preview.
Use this preview to determine:
 - The number of phase-encode lines collected.
 - The correct offset (if any) to apply.
Update these values in your configuration file accordingly.

### Loading packages and data

In [1]:
import yaml
import numpy as np
import utils.data_ingestion as di
import utils.gif as gif
from IPython.display import display

def load_config(config_file="config.yaml"):
    with open(config_file, "r") as f:
        config = yaml.safe_load(f)
    return config

config = load_config()

# Set the file paths (or load from a temporary config file if you wish)
twix_file = config["data"]["twix_file"]
dicom_folder = config["data"]["dicom_folder"]

# Read TWIX file and extract k-space data
scans = di.read_twix_file(twix_file, include_scans=[-1], parse_pmu=False)

Software version: VD/VE (!?)

Scan  1


100%|██████████| 670M/670M [00:00<00:00, 1.33GB/s]

Read 1 scans from meas_MID00086_FID26450_DMI_PMU_250216_100rep.dat


### Extracting k-space data, zero-filling, and displaying

In [2]:
kspace = di.extract_image_data(scans)

n_frames = di.get_num_frames(dicom_folder)
n_coils = kspace.shape[1]

# Reshape into frames
kspace = np.reshape(kspace, (n_frames, -1, kspace.shape[1], kspace.shape[2]))

extended_pe_lines = di.get_total_phase_encodes(dicom_folder)
offset = 0

# Zero fill
kspace_zf = np.zeros((n_frames, extended_pe_lines, n_coils, 256), dtype=np.complex64)
kspace_zf[:, offset:offset+kspace.shape[1], :] = kspace

# Use the GIF function to display the zero-filled k-space preview.
display(gif.display_kspace_as_gif(kspace_zf, duration=0.2))

Extracted image data shape: (11200, 30, 256)
Found 100 DICOM frames in folder SE00078001 DMI_PMU_250216_100REP
Total phase encodes from AcquisitionMatrix: 128
